# Komputerowe wspomaganie tłumaczenia

# Zajęcia 11 - urównoleglanie

Na poprzednich zajęciach poznaliśmy techniki pozyskiwania tekstu z Internetu. Jeśli uda nam się w ten sposób pozyskać tekst w jednym języku oraz jego tłumaczenie na inny język, jesteśmy tylko o krok od uzyskania najbardziej przydatnego zasobu z punktu widzenia wspomagania tłumaczenia - pamięci tłumaczeń. Krokiem tym jest automatyczne urównoleglanie tekstu.

Automatyczne urównoleglanie tekstu składa się z dwóch kroków:
1. Podziału tekstu źródłowego oraz docelowego na zdania.
2. Dopasowaniu zdań źródłowych do docelowych.

Zdania, o których mowa w punkcie 1., powinniśmy rozumieć jako segmenty, tj. niekoniecznie kompletne zdania w sensie gramatycznym. Standardowym sposobem podziału tekstu na segmenty jest dzielenie po znaku nowej linii lub zaraz po kropce, o ile jest ona częścią sekwencji: ".[spacja][Wielka litera]"

### Ćwiczenie 1: Zaimplementuj podstawowy algorytm segmentacji tekstu. Użyj odpowiedniego wyrażenia regularnego, łapiącego wielkie litery w dowolnym języku, np. "Ż" (użyj klasy unikodowej). Zwróć listę segmentów.

In [2]:
import regex as re

def segment_text(text):
    regex = re.compile(r'\p{Lu}')
    positions = [match.start() for match in regex.finditer(text)]
    positions.insert(0, 0)
    positions.append(len(text))
    segments = [text[positions[i]:positions[i+1]].strip() for i in range(len(positions)-1)]

    return segments

text = "To jest próba. Test musi byc wykonany. Wszystko jest okey. Źródło wody. Ósemka"
segments = segment_text(text)
for segment in segments:
    print(segment)



To jest próba.
Test musi byc wykonany.
Wszystko jest okey.
Źródło wody.
Ósemka


### Ćwiczenie 2: Uruchom powyższy algorytm na treści wybranej przez siebie strony internetowej (do ściągnięcia treści strony wykorzystaj kod z laboratoriów nr 7). Zidentyfikuj co najmniej dwa wyjątki od ogólnej reguły podziału na segmenty i ulepsz algorytm.

In [6]:
import requests
from bs4 import BeautifulSoup


def segment_text(text):    

    pattern = r'(\p{Lu}\p{Ll}*|\b\p{Lu}(?=\p{Ll}))'
    regex = re.compile(pattern, re.UNICODE)

    matches = list(regex.finditer(text))

    segments = []
    start = 0
    for match in matches:
        end = match.start()
        if start < end:
            segments.append(text[start:end].strip())
        start = end

    segments.append(text[start:].strip())

    segments = [segment for segment in segments if segment]

    return segments

def sentence_split_enhanced(url):
    soup = BeautifulSoup(requests.get(url).content, 'html.parser')
    text = re.sub(r"\s+", " ", soup.get_text())
    segments = segment_text(text)
    return segments

sentence_split_enhanced("https://epoznan.pl")

# problem z wyrazami, które sa pisane duza litera 
# problem z nazwami ulic

['epoznan.pl - pierwszy portal',
 'Poznania',
 'Wyszukaj',
 'Zaloguj',
 'Login',
 'Hasło',
 'Zapomniałeś hasła?',
 'Zaloguj',
 'Nie masz konta?',
 'Zarejestruj się',
 'Wiadomości kronika policyjna inwestycje nieruchomości biznes polityka komunikacja wywiady kultura historia life style region pogoda',
 'Pogoda',
 'Sport',
 'Kultura i rozrywka',
 'Korki',
 'Forum',
 'Kontakt 1 godzina temu',
 'Zbierają niezbędne rzeczy dla pogorzelców z ul.',
 'Promienistej.',
 'Ogień strawił dorobek życia 31 1 godzina temu',
 'Korek na',
 'A2.',
 'Blokada jednego pasa ruchu z powodu stłuczki 28 1 godzina temu',
 'Spore utrudnienia za węzłem autostradowym.',
 'Kierowca samochodu wjechał w bariery.',
 'Ranna jedna osoba 11 2 godziny temu "',
 'Cisza dzieciaki, cichutko!".',
 'Idzie',
 'Magda',
 'Gessler.',
 'Kolejne rewolucje w',
 'Wielkopolsce 41 2 godziny temu',
 'Poszukujesz rehabilitacji - przyjęcie w 72 godziny',
 'Reklama 4 3 godziny temu',
 'Wielki turniej piłki siatkowej nad',
 'Rusałką.',
 'Kibic

Po podziale tekstu na segmenty po stronie źródłowej oraz docelowej, możemy przystąpić do kroku drugiego - dopasowania segmentów. Głównym wyzwaniem tego kroku jest fakt, iż po stronie źródłowej może być inna liczba segmentów, niż po stronie docelowej. Takie rozbieżności są bardzo częste, a wynikają między innymi z:
* tłumaczenia jednego zdania źródłowego przy użyciu więcej niż jednego zdania
* tłumaczenia więcej niż jednego zdania źródłowego przy użyciu jednego zdania
* pominięcia zdania podczas tłumaczenia
* rozbieżności pomiędzy wersjami tekstu źródłowego i docelowego (np. tekst źródłowy mógł być modyfikowany po przetłumaczeniu i tłumaczenie nie zostało zaktualizowane)
* przetłumaczenia tekstu źródłowego tylko częściowo

Problemy te rozwiązwyane są na różne sposoby. Najpopularniejszym programem do przeprowadzania urównoleglania jest [Hunalign](https://github.com/danielvarga/hunalign). Wejściem do programu są dwa pliki, zawierające po jednym segmencie w linii. Wyjściem - plik urównoleglony w wewnętrznym formacie hunaligna.

### Ćwiczenie 3: Odnajdź dowolną stronę, która jest dostępna w wielu językach. Pobierz z tej strony tekst oryginalny (tylko ze strony głównej) oraz przetłumaczony na dowolny inny język. Przy użyciu Pythona przygotuj pliki dla Hunaligna i uruchom go.

Wyjściem z Hunaligna jest plik w specjalnym formacie Hunaligna. Problem jednak w tym, że niestety nie można go w prosty sposób zaimportować do jakiegokolwiek narzędzia typu CAT. Potrzebna jest konwersja do któregoś z bardziej popularnych formatów, np. XLIFF.

XLIFF jest formatem do przechowywania pamięci tłumaczeń, który opiera się na XML-u. Przykładowy plik XLIFF wygląda następująco:

In [11]:
def create_hunaligna_file(text_en, text_pl, output_file):
    sentences_en = text_en.split('. ')
    sentences_pl = text_pl.split('. ')

    with open(output_file, "w", encoding="utf-8") as f:
        f.write("# Sentence pairs\n")
        for i, (en, pl) in enumerate(zip(sentences_en, sentences_pl)):
            f.write(f"{i}\n")
            f.write("# Source\n")
            f.write(f"{en.strip()}\n")
            f.write("# Target\n")
            f.write(f"{pl.strip()}\n")


en_url = "https://www.apple.com"
pl_url = "https://www.apple.com/pl/"

en_text = ' '.join(sentence_split_enhanced(en_url))
pl_text = ' '.join(sentence_split_enhanced(pl_url))

with open("txt/en.txt", "w", encoding="utf-8") as f_en:
    f_en.write(en_text)

with open("txt/pl.txt", "w", encoding="utf-8") as f_pl:
    f_pl.write(pl_text)

create_hunaligna_file(en_text, pl_text, "txt/hunaligna.txt")



### Ćwiczenie 4: Napisz konwerter formatu hunaligna na XLIFF.

In [18]:
import xml.etree.ElementTree as ET

def convert2xliff():
    segments = []
    with open('txt/hunaligna.txt', 'r', encoding='utf-8') as file:
        segment = {}
        for line in file:
            line = line.strip()
            if line.startswith("# Source"):
                segment['source'] = next(file).strip()
            elif line.startswith("# Target"):
                segment['target'] = next(file).strip()
                segments.append(segment)
                segment = {}
            
    xliff = ET.Element('xliff', version="1.2")
    file_elem = ET.SubElement(xliff, 'file', {
    'datatype': "plaintext",
    'original': "file.txt",
    'source-language': 'en',
    'target-language': 'pl'
    })
    body = ET.SubElement(file_elem, 'body')

    for i, segment in enumerate(segments):
        trans_unit = ET.SubElement(body, 'trans-unit', id=str(i))
        source = ET.SubElement(trans_unit, 'source')
        source.text = segment['source']
        target = ET.SubElement(trans_unit, 'target')
        target.text = segment['target']

    tree = ET.ElementTree(xliff)
    tree.write('txt/output.xliff', encoding='UTF-8', xml_declaration=True)


convert2xliff()


